# Quant Trading - Crypto (Part 5) 

In [18]:
# Import packages
import pandas as pd
import numpy as np
import datetime
import random
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import norm
import Backtest_lib
import importlib
importlib.reload(Backtest_lib)


<module 'Backtest_lib' from 'c:\\Users\\dpalc\\OneDrive - Flow Energia\\Área de Trabalho\\Projetos\\Quant Trading\\Crypto Trading\\Artigo\\Backtest_lib.py'>

## Forward Testing

In [20]:
# Define initial parameters
filepath = "historical_data_BTCUSDT_1h.xlsx"
symbol = "BTCUSDT"
tc = -0.001
testing_months = 12
training_start = "2017-01-01"
training_end = None

walk_forward_results = pd.DataFrame()

# Loop periods
for i in range(5):

    if training_end:
        pass
    else:
        training_months = 12 
        training_end_date = pd.to_datetime(training_start) + pd.DateOffset(months=training_months)
        training_end = datetime.datetime.strftime(training_end_date, "%Y-%m-%d")
    
    print("Training:", training_start, training_end)


    # Create new object and run parametric analysis
    trainer = Backtest_lib.MA_Backtester(filepath = filepath, symbol = symbol,
                                start = training_start, end = training_end, tc = tc)

    trainer.parametric_analysis(SMA_S_range = (10, 40, 10), 
                            SMA_M_range = (50, 200, 50),
                            SMA_L_range = (200, 1000, 200))

    # Get the one with the highest winning percentage
    best = trainer.results_overview.sort_values(by='Winning Percentage', ascending=False).iloc[0,]

    sma_s = best['SMA_S'].astype(int)
    sma_m = best['SMA_M'].astype(int)
    sma_l = best['SMA_L'].astype(int)

    # Start testing from where training stopped
    testing_start_date = pd.to_datetime(training_end)
    testing_start = training_end
    testing_end_date = testing_start_date + pd.DateOffset(months=testing_months)
    testing_end = datetime.datetime.strftime(testing_end_date, "%Y-%m-%d")

    print("Testing:", testing_start, testing_end)

    # Create new object and test strategy
    tester = Backtest_lib.MA_Backtester(filepath = filepath, symbol = symbol,
                                start = testing_start, end = testing_end, tc = tc)

    tester.test_strategy(smas = (sma_s, sma_m, sma_l), print_result=False)
    
    # Store results in the dataframe
    walk_forward_results = pd.concat([walk_forward_results, tester.results], ignore_index=False)
    
    # Define training end for the next loop
    training_end = testing_end


Training: 2017-01-01 2018-01-01
Testing: 2018-01-01 2019-01-01
Training: 2017-01-01 2019-01-01
Testing: 2019-01-01 2020-01-01
Training: 2017-01-01 2020-01-01
Testing: 2020-01-01 2021-01-01
Training: 2017-01-01 2021-01-01
Testing: 2021-01-01 2022-01-01
Training: 2017-01-01 2022-01-01
Testing: 2022-01-01 2023-01-01


In [21]:
# Calculate relevant metrics
walk_forward_results["creturns"] = walk_forward_results["returns"].cumsum().apply(np.exp)
walk_forward_results["cstrategy"] = walk_forward_results["strategy"].cumsum().apply(np.exp)

walk_forward_results['Max Return'] = walk_forward_results['cstrategy'].cummax()
walk_forward_results['Drawdown'] = (walk_forward_results['cstrategy'] / walk_forward_results['Max Return']) - 1

walk_forward_results['cstrategy'].ffill(inplace=True)

walk_forward_results.head()

Close   returns     SMA_S       SMA_M         SMA_L  \
Date                                                                          
2018-01-17 16:00:00  10287.97  0.108790  9948.061  12667.7579  14213.995875   
2018-01-17 17:00:00   9849.99 -0.043505  9856.559  12620.9792  14204.798325   
2018-01-17 18:00:00   9650.00 -0.020513  9769.355  12573.9043  14195.915675   
2018-01-17 19:00:00  10390.00  0.073886  9783.355  12535.3917  14188.565225   
2018-01-17 20:00:00  10901.06  0.048016  9902.466  12502.3123  14182.292800   

                     position  strategy  trades  creturns  cstrategy  \
Date                                                                   
2018-01-17 16:00:00        -1       NaN     0.0  1.114929        NaN   
2018-01-17 17:00:00        -1  0.043505     0.0  1.067464   1.044465   
2018-01-17 18:00:00        -1  0.020513     0.0  1.045790   1.066111   
2018-01-17 19:00:00        -1 -0.073886     0.0  1.125986   0.990180   
2018-01-17 20:00:00        -1 -0.048016     0.0  1.181370   0.943759   

                     Max Return  Drawdown  
Date                                       
2018-01-17 16:00:00         NaN       NaN  
2018-01-17 17:00:00    1.044465  0.000000  
2018-01-17 18:00:00    1.066111  0.000000  
2018-01-17 19:00:00    1.066111 -0.071222  
2018-01-17 20:00:00    1.066111 -0.114765

In [22]:
# Calculate other metrics and show results
tester.results = walk_forward_results

strategy_multiple = round(tester.calculate_multiple(tester.results.strategy), 6)
bh_multiple =       round(tester.calculate_multiple(tester.results.returns), 6)
outperf =           round(strategy_multiple - bh_multiple, 6)
cagr =              round(tester.calculate_cagr(tester.results.strategy), 6)
ann_mean =          round(tester.calculate_annualized_mean(tester.results.strategy), 6)
ann_std =           round(tester.calculate_annualized_std(tester.results.strategy), 6)
sharpe =            round(tester.calculate_sharpe(tester.results.strategy), 6)
total_trades =      tester.calculate_total_trades()
max_drawdown =      round(tester.calculate_mdd(), 2)
winning_percentage= round(tester.calculate_winning_percentage()*100, 2)

metrics = {'Strategy Multiple':[strategy_multiple], 
                'Outperformance':[outperf], 
                'CAGR':[cagr],
                'Annualized Mean':[ann_mean],
                'Annualized Std':[ann_std],
                'Sharpe Ratio':[sharpe],
                'Total Trades':[total_trades],
                'Max Drawdown':[max_drawdown],
                'Winning Percentage':[winning_percentage]}

metrics = pd.DataFrame(metrics)

display(metrics)

# Rename columns and plot results
walk_forward_results.rename(columns={'creturns': 'Buy and Hold', 'cstrategy':'Strategy'}, inplace=True)

fig = px.line(walk_forward_results,
        x=walk_forward_results.index,
        y=['Buy and Hold', 'Strategy'])
fig.update_layout(xaxis_title="Date", yaxis_title="Normalized Returns")
fig.show()

Strategy Multiple  Outperformance      CAGR  Annualized Mean  \
0           5.555502           3.537  0.447031         0.388846   

   Annualized Std  Sharpe Ratio  Total Trades  Max Drawdown  \
0        0.644593       0.69351           648        -54.65   

   Winning Percentage  
0               45.61

## Statistical Significance - Drunk Trader

In [10]:
strategy_multiple_list = []
returns_df = pd.DataFrame()
returns_df['Strategy Returns'] = walk_forward_results['Strategy']

for i in range(100000):
    # Define the number of hours and the maximum number of trades
    num_values = len(tester.results)
    max_changes = total_trades

    # Create a list of zeros
    values = [0] * num_values

    # Generate random trades hours
    change_indices = sorted(random.sample(range(num_values), max_changes))

    # Set the initial value to 0
    current_value = 0

    # Loop through the trades indices and update the values
    for index in change_indices:
        value = random.choice([-1, 0, 1])
        values[current_value:index] = [value] * (index - current_value)
        current_value = index

    # Replace the position column with the random values and run backtest
    tester.results["position"] = values
    tester.run_backtest()
    tester.results["cstrategy"] = tester.results["strategy"].cumsum().apply(np.exp)

    # Uncomment this cell to store the random returns in a dataframe
    #returns_df["Random_{}".format(i)] = tester.results["cstrategy"]

    # Calculate the multiple and store it in the list
    strategy_multiple = round(tester.calculate_multiple(tester.results.strategy), 6)   
    strategy_multiple_list.append(strategy_multiple)




In [16]:
# Get strategy multiple and drunk trader 95th percentile results
multiple_value = walk_forward_results['Strategy'].iloc[-1]
p = np.percentile(strategy_multiple_list, 95)

# Plot histogram highlighting both values above
fig = px.histogram(x=strategy_multiple_list)
fig.add_vline(x=p, line_width=3, line_dash="dash", line_color="red")
fig.add_vline(x=multiple_value, line_width=3, line_dash="dash", line_color="green")
fig.update_layout(xaxis_title="Normalized Results")
fig.show()

In [6]:
# Show total trades
total_trades

648

In [17]:
# Create line plot to show cumulative returns of the random positions in time

#fig = px.line(returns_df,
#        x=returns_df.index,
#        y=returns_df.columns[0:100])

#fig.update_layout(xaxis_title="Date", yaxis_title="Normalized Returns")
#fig.show()